In [1]:
import findspark
findspark.init()
import pyspark
import re
import json
import pysolr
import datetime

In [2]:
#sc.stop()

In [3]:
sc = pyspark.SparkContext("local[*]",appName = "Freebase_people")

In [4]:
#subor = "freebase-head-1000000"
subor = "freebase-head-10000000"
#subor = "freebase-head-100000000"

In [5]:
re_name = '(\/[gm]\..+\t<http:\/\/rdf\.freebase\.com\/ns\/type\.object\.name>\t\".*\"@en)'
re_alias = '(\/[gm]\..+\t<http:\/\/rdf\.freebase\.com\/ns\/common\.topic\.alias>\t\".*\"@en)'
re_birth = '(\/[gm]\..+\t<http:\/\/rdf\.freebase\.com\/ns\/people\.person\.date_of_birth>\t)'
re_death = '(\/[gm]\..+\t<http:\/\/rdf\.freebase\.com\/ns\/people\.deceased_person\.date_of_death>\t)'

In [6]:
people = sc.textFile(subor).filter(lambda x: re.search(re_name,x) or re.search(re_alias,x) or re.search(re_birth,x) or re.search(re_death,x)).distinct()

In [7]:
people.count()

96554

In [8]:
people.take(20)

['<http://rdf.freebase.com/ns/g.112yfxf28>\t<http://rdf.freebase.com/ns/common.topic.alias>\t"Yuko Ootaki"@en\t.',
 '<http://rdf.freebase.com/ns/g.113qbgpm2>\t<http://rdf.freebase.com/ns/people.person.date_of_birth>\t"1968-04-10"^^<http://www.w3.org/2001/XMLSchema#date>\t.',
 '<http://rdf.freebase.com/ns/g.119pfy3js>\t<http://rdf.freebase.com/ns/people.person.date_of_birth>\t"1952-10-17"^^<http://www.w3.org/2001/XMLSchema#date>\t.',
 '<http://rdf.freebase.com/ns/g.11b5v29kyk>\t<http://rdf.freebase.com/ns/people.person.date_of_birth>\t"1822-04-22"^^<http://www.w3.org/2001/XMLSchema#date>\t.',
 '<http://rdf.freebase.com/ns/g.11b6377dz8>\t<http://rdf.freebase.com/ns/people.person.date_of_birth>\t"1428"^^<http://www.w3.org/2001/XMLSchema#gYear>\t.',
 '<http://rdf.freebase.com/ns/g.11b66gnszy>\t<http://rdf.freebase.com/ns/people.person.date_of_birth>\t"1419"^^<http://www.w3.org/2001/XMLSchema#gYear>\t.',
 '<http://rdf.freebase.com/ns/g.11b6_p5czs>\t<http://rdf.freebase.com/ns/people.person.

In [9]:
datalist = sorted(people.collect())

In [10]:
#file_short = 'people_data_1_mil.txt'
file_short = 'people_data_10_mil.txt'
#file_short = 'people_data_100_mil.txt'

with open(file_short, 'w', encoding="utf-8") as file:
    file.writelines("%s\n" % item for item in datalist)
file.close()

In [11]:
#file_path = 'json_1_mil.json'
file_path = 'json_10_mil.json'
#file_path = 'json_100_mil.json'

In [12]:
file = open(file_short,"r",encoding='utf-8')
json_file = open(file_path,'w',encoding='utf8')

In [17]:
data_holder = []
current_subject = None
while 1:
    line = file.readline()
    #print(line)
    
    if not line:
        break
        
    subject = re.search('(\/[gm]\..+)',line[27:line.find(">")]).group(0)
    print('subject: ' ,subject)
    
    if current_subject == None:
        current_subject = ObjectInfo(subject)
    
    elif current_subject.id_ != subject: 
        print('write')
        current_subject.dob, current_subject.dod = check_dates(current_subject)
        
        if (current_subject.name != [] and (current_subject.dob != '0' or current_subject.dod != '0')):
            append_data(current_subject)
            
        current_subject = ObjectInfo(subject)
       
    predicate = re.split('\t',line)
    predicate = re.split("\/",predicate[1])
    predicate = predicate[len(predicate)-1]

    value = re.split('\t',line)
    if re.search('type\.object\.name.+', predicate):
        #print('pred: ', predicate)
        #current_subject.name = re.search('\".*\"',value[2]).group(0).replace('\"','')
        current_subject.name.append(re.search('\".*\"',value[2]).group(0).replace('\"',''))
        #print('id: ', current_subject.id_, current_subject.name, current_subject.dob)
    if re.search('common\.topic\.alias.+', predicate):
        #print('pred: ', predicate)
        #current_subject.alias = re.search('\".*\"',value[2]).group(0).replace('\"','')
        current_subject.alias.append(re.search('\".*\"',value[2]).group(0).replace('\"',''))
        print('alias: ', current_subject.alias) 
    if re.search('people\.person\.date.+', predicate):
        #print('pred: ', predicate)
        current_subject.dob = re.search('\".*\"',value[2]).group(0).replace('\"','')
        #print('dob: ', current_subject.dob)
    if re.search('people\.deceased_person\.date.+', predicate):
        #print('pred: ', predicate)
        current_subject.dod = re.search('\".*\"',value[2]).group(0).replace('\"','')
        #print('dod: ', current_subject.dod)
write_json()

subject:  /g.112yf8_qt
subject:  /g.112yf8_qt
subject:  /g.112yfhv9p
write
subject:  /g.112yfhv9p
subject:  /g.112yfj_hx
write
subject:  /g.112yfjql4
write
subject:  /g.112yfjql4
subject:  /g.112yfl85l
write
subject:  /g.112yfmpf8
write
subject:  /g.112yfmpf8
subject:  /g.112yfpbtx
write
subject:  /g.112yfqr32
write
subject:  /g.112yfqr32
subject:  /g.112yfsjp0
write
subject:  /g.112yftq1m
write
subject:  /g.112yftq1m
subject:  /g.112yfxf28
write
alias:  ['Yuko Ohtaki']
subject:  /g.112yfxf28
alias:  ['Yuko Ohtaki', 'Yuko Ootaki']
subject:  /g.112yfxf28
subject:  /g.112yfxf28
subject:  /g.112yfxkgx
write
['Yuko Ohtaki', 'Yuko Ootaki']
Ootaki, Yuuko
subject:  /g.112yfy2xr
write
subject:  /g.112yfysbz
write
Guilty Pleasures Love
subject:  /g.112yfysbz
subject:  /g.112yg02f0
write
subject:  /g.112yg02f0
subject:  /g.112yg0_tf
write
subject:  /g.112yg1rpk
write
subject:  /g.112yg1rpl
write
subject:  /g.112yg1rpl
subject:  /g.112yg4kzv
write
subject:  /g.112yg50rd
write
subject:  /g.112yg5x

write
11 y 6 (dancefloor mix)
subject:  /g.11b7_lpdzn
write
Wake Up and Watch me Leave
subject:  /g.11b7_lpf16
write
Remember Then! 25 Original Classics
subject:  /g.11b7_lq09p
write
Slowly, Slowly Thunder
subject:  /g.11b7_lqmg9
write
Jewish Symphony
subject:  /g.11b7_lqmgx
write
Lala & Lili
subject:  /g.11b7_lqmrd
write
To Be Young, Gifted and Black
subject:  /g.11b7_lr7_t
write
Mental Beats
subject:  /g.11b7_lr89v
write
Hello Lola!
subject:  /g.11b7_lr8l4
write
Tendercare
subject:  /g.11b7_lrxqw
write
Moonlight Kid
subject:  /g.11b7_lrxzh
write
Kaede
subject:  /g.11b7_lsh2n
write
Order Shall Prevail
subject:  /g.11b7_lshdk
write
Stories Bored Ignored
subject:  /g.11b7_lshky
write
20121228
subject:  /g.11b7_lt3w5
write
Terendap Laraku
subject:  /g.11b7_lt4f7
write
Mal de Mer
subject:  /g.11b7_lt4hk
write
Toto Berizo
subject:  /g.11b7_lv_md
write
Midnight Matinée (Bassface Sascha Relik)
subject:  /g.11b7_lv_mg
write
Genie Dance
subject:  /g.11b7_lv_vb
write
Vaciado
subject:  /g.11b7_l

write
Fear of the Night (Medley)
subject:  /g.11b821yhxl
write
Sapphire Bullets of Pure Love
subject:  /g.11b821yjfr
write
Big Big City
subject:  /g.11b821yjfz
write
Dancing on the Table
subject:  /g.11b821zcd6
write
Story
subject:  /g.11b821zcpx
write
If You Are for Us
subject:  /g.11b821zcr9
write
Tears
subject:  /g.11b821zcwy
write
Fall a Little Harder
subject:  /g.11b821zd0q
write
Reverie
subject:  /g.11b821zd3h
write
Truth Hurts While Laying on Your Back
subject:  /g.11b821zd7y
write
Believe in Me (Cass & Mangan remix)
subject:  /g.11b82200vy
write
It's Over (extended version)
subject:  /g.11b822012n
write
Wild Side Of Life
subject:  /g.11b82201r1
write
Six poèmes extraits d'Alcools d'Apollinaire: L’Adieu
subject:  /g.11b8220wy1
write
I Want You to Be My Baby
subject:  /g.11b8220xqx
write
Cigarette After
subject:  /g.11b8220xsz
write
Intro Menu
subject:  /g.11b8221r3y
write
Healthy Mama
subject:  /g.11b8222m63
write
Define
subject:  /g.11b8222m8b
write
I'm Gonna Getcha Good
subjec

subject:  /g.11bc15n975
write
Cornelia Franchoys
subject:  /g.11bc15t0rq
write
Exe Broadcasting Ltd.
subject:  /g.11bc15t0w6
write
Dr Frederic Poynton Weaver
subject:  /g.11bc168pcy
write
Edgar Henry Brown, Jr.
subject:  /g.11bc16b9x8
write
Hewavitharana Dingiri Appuhamy
subject:  /g.11bc16j1j_
write
Thyrza Beer
subject:  /g.11bc16kwfz
write
Paul Angoulvent
subject:  /g.11bc16kwvq
write
Ba Tha
subject:  /g.11bc16p_92
write
Milena Medvešek
subject:  /g.11bc16p_kb
write
Samuel Trott
subject:  /g.11bc16p_p4
write
Antonio Martelli
subject:  /g.11bc16rpd6
write
Princess Susan
subject:  /g.11bc16t9nr
write
Ofovwe Imoukhuede
subject:  /g.11bc16zq37
write
Sridevi Kesavan
subject:  /g.11bc17f6yp
write
Roxane Cohen Silver
subject:  /g.11bc17kjdy
write
monte Calarighe
subject:  /g.11bc17zs87
write
Lawrence Chinese Evangelical Church
subject:  /g.11bc17zslj
write
Manitoba Professional Hockey League
subject:  /g.11bc17zsqc
write
Aunofo Siuli Atuilagi
subject:  /g.11bc18jjlq
write
'Yaar' Kannan
subj

subject:  /g.11bv1m0cwn
write
Gotta Boyfriend?
subject:  /g.11bv1m1jl0
write
Sacre l'amour
subject:  /g.11bv1m1k3d
write
Shoelace (original demo)
subject:  /g.11bv1m1k5r
write
Silver Sea
subject:  /g.11bv1m1k78
write
Sucker for the Witch
subject:  /g.11bv1m1k7m
write
Emily
subject:  /g.11bv1m1kqv
write
Titan♀~9chiku
subject:  /g.11bv1m1lkd
write
Ruins
subject:  /g.11bv1m3c47
write
Jazz Jungle
subject:  /g.11bv1m3c_w
write
I Don't Know How to Love Him
subject:  /g.11bv1m3cyl
write
She's Like Heroin to Me
subject:  /g.11bv1m3dc4
write
Open Up
subject:  /g.11bv1m3dgv
write
Disco Suicide
subject:  /g.11bv1m3dhl
write
In My Mind
subject:  /g.11bv1m3dsb
write
Knife Wound (Live From a Secret Underground Bunker to the Last Bastion of Humanity on This Earth)
subject:  /g.11bv1m3dtm
write
Get Off My Dick and Tell Yo Bitch to Come Here
subject:  /g.11bv1m3dtv
write
Intro
subject:  /g.11bv1m3dxk
write
Introduction
subject:  /g.11bv1m3dyp
write
Baby I Love You
subject:  /g.11bv1m3f2v
write
First fo

...

subject:  /m.080ty95
write
9780525444107
subject:  /m.080tz06
write
Exit the rainmaker
subject:  /m.080tzhr
write
Elton Trueblood: believer, teacher, and Friend
subject:  /m.080v1pz
write
9780829808520
subject:  /m.080v6hz
write
9780896382398
subject:  /m.080v_dt
write
9780814655832
subject:  /m.080vg_l
write
9780822522584
subject:  /m.080vmn6
write
A South Carolina chronology, 1497-1992
subject:  /m.080vmn_
write
Desertification: natural background and human mismanagement
subject:  /m.080vrvj
write
9780688020132
subject:  /m.080vsqy
write
9781879967014
subject:  /m.080vw1f
write
9781558703810
subject:  /m.080vwgn
write
9780307101006
subject:  /m.080vxnp
write
9781881604013
subject:  /m.080w17r
write
9781854772145
subject:  /m.080w1b0
write
9780521566681
subject:  /m.080w22g
write
9788433910356
subject:  /m.080w31s
write
9780570049784
subject:  /m.080w5wm
write
9780205267743
subject:  /m.080w6bp
write
9780764501425
subject:  /m.080wcmy
write
French art
subject:  /m.080wjk
write
9783579

subject:  /m.08221t
write
9781581080247
subject:  /m.08222t0
write
Rich's
subject:  /m.082273n
write
9781584650782
subject:  /m.0822hcn
write
9781592796922
subject:  /m.0822tj
write
9781843231967
subject:  /m.0822tj
subject:  /m.0822tj
subject:  /m.0822v0s
write
[]
Daniel Topolski
subject:  /m.0822wg8
write
9781859609613
subject:  /m.08235l
write
9781861343239
subject:  /m.0823gz3
write
Midland Railway 1377 Class
subject:  /m.0823hzg
write
9782020535601
subject:  /m.0823l5v
write
9782070530984
subject:  /m.0823m9b
write
9782234055049
subject:  /m.0823pqy
write
9782264029812
subject:  /m.0823sbz
write
9782742405657
subject:  /m.0823swp
write
9782870271216
subject:  /m.08243tt
write
9782884790598
subject:  /m.0824c49
write
9788408010463
subject:  /m.0824d72
write
Mapping the Contours of Oppression: Subjectivity, Truth and Fiction in Recent German Autobiographical Treatments of Totalitarianism (Amsterdamer Publikationen ... Publikationen Zur Sprache Und Literatur)
subject:  /m.0824dpc
wri

write
9789076244068
subject:  /m.082z7xr
write
9789500407588
subject:  /m.082z87
write
Fundamentals of microfabrication: the science of miniaturization
alias:  ['Cognitive Complexity Theory']
subject:  /m.082z87
subject:  /m.082z9gb
write
Cognitive complexity
subject:  /m.082zbdl
write
The dark ship
subject:  /m.082zd63
write
9780802852496
subject:  /m.082zmkp
write
Introduction to plant physiology
subject:  /m.082zn80
write
9780312277307
subject:  /m.082zs4f
write
9781570719370
subject:  /m.082zv5z
write
9780199279548
subject:  /m.082zx0r
write
9781416537830
subject:  /m.08300cc
write
9781557288790
subject:  /m.0830119
write
9780534005436
subject:  /m.08301_t
write
9780516087542
subject:  /m.08301dt
write
ITPA: clinical interpretation and remediation
subject:  /m.08301qx
write
9780810450998
subject:  /m.08307lw
write
9780198533504
subject:  /m.083085k
write
9780170050654
subject:  /m.0830l35
write
9789024719419
subject:  /m.0830l4
write
9780812278125
subject:  /m.0830z5q
write
Good-mo

subject:  /m.0842g9m
write
9780877957072
subject:  /m.0842qs6
write
Developing effective student services programs
subject:  /m.0842t9r
write
Uzbekistan at the 2006 Winter Olympics
subject:  /m.0842vqf
write
Belgium at the 2004 Summer Olympics
subject:  /m.0842xxf
write
France at the 1924 Winter Olympics
subject:  /m.0842y6t
write
9780942568165
subject:  /m.0842z1s
write
Bunyip aristocracy: the New South Wales constitution debate of 1853 and hereditary institutions in the British colonies
subject:  /m.0842z8r
write
9781557110367
subject:  /m.0842znz
write
The literary culture of nonconformity in later seventeenth-century England
subject:  /m.08431gw
write
Per Aspera Press vs Per Aspera Press
subject:  /m.08433pt
write
9780374257316
subject:  /m.08436t3
write
Women artists in history: from antiquity to the 20th century
subject:  /m.08437hl
write
9781852740269
subject:  /m.08437kw
write
9780671669492
subject:  /m.0843_jv
write
9780201546118
subject:  /m.0843bty
write
9781550960679
subjec

write
9781854142177
subject:  /m.084nsk2
write
9781854724472
subject:  /m.084nv7w
write
9781862870857
subject:  /m.084nxsh
write
9781873712665
subject:  /m.084p2l3
write
9781885061256
subject:  /m.084p591
write
9781931696944
subject:  /m.084p7cc
write
9782210721128
subject:  /m.084p8_j
write
Associés contre le crime
subject:  /m.084p8bh
write
Coyote attend
subject:  /m.084prs0
write
Martin Rattigan
subject:  /m.084q408
write
9789998285521
subject:  /m.084q54
write
The debates on the Grand Remonstrance, November and December  1641: with an introductory essay on English freedom under Plantagenet  and Tudor sovereigns.
subject:  /m.084q9n1
write
A Man Escaped
subject:  /m.084q_1x
write
9781894022293
subject:  /m.084qmn2
write
9781590172018
subject:  /m.084qnmk
write
9781561451081
subject:  /m.084qt80
write
9780875527420
subject:  /m.084qy2s
write
9781562925345
subject:  /m.084r_3p
write
9780314957818
subject:  /m.084rry9
write
9780434958702
subject:  /m.084rvk0
write
9780723214717
subject

In [22]:
def write_json():
    json_ = json.dumps(data_holder, indent=4, ensure_ascii=False)
    json_file.write(json_)
    json_file.close()

In [14]:
class ObjectInfo:
    id_ = None
    name = None
    alias = None
    dob = '0'
    dod = '0'
     
    def __init__(self, id_):
        self.id_ = id_
        self.name = []
        self.alias = []
        dob = '0'
        dod = '0'

In [15]:
def check_dates(current_subject):
    dob = current_subject.dob.replace('-','')
    dod = current_subject.dod.replace('-','')
    
    if dob == '0' and dod == '0':
        return dob,dod

    if 0 < int(dob) < 10000:
        dob = dob + '0101'
    if 0 < int(dod) < 10000:
        dod = dod + '0101'

    if dob == '0':        
        dob = str(int(dod) - 1000000)
    if dod == '0':
        dod = str(int(dob) + 1000000)

    if dob != '0' and dod != '0':
        return str(dob),str(dod)

In [16]:
def append_data(current_object):
    #print(current_object.id_)
    #print(current_object.name)
    #print(current_object.alias)
    #print(current_object.dob)
    #print(current_object.dod)
    data = None
    data = { 
        "name": current_object.name, 
        "alias": current_object.alias, 
        "birth": current_object.dob, 
        "death": current_object.dod 
    }
    data_holder.append(data)        

In [ ]:
#re.search('\/(?P<subject>[gm]\..+)>.+\/type\.object\.name>',line)
#re.search('\/(?P<http://rdf\\.freebase\\.com/ns/[gm]\..+)>.+\/type\.object\.name>',line)

In [18]:
#url = 'http://localhost:8983/solr/freebasecore_1mil/'
url = 'http://localhost:8983/solr/freebasecore_10mil/'

In [19]:
mysolr = pysolr.Solr(url)

In [ ]:
meno = 'Hiromi Wada'
q = 'name:*' + meno + '*'
print(q)
vysledok_ = mysolr.search(q=q)
list(vysledok_)

In [20]:
vysledok = mysolr.search(q='name:*Hiromi Wada*')
vysledok2 = mysolr.search(q='alias:*Ohtaki*')

In [21]:
for line in vysledok:
    osoba_1, alias_1, dob_1, dod_1 = line['name'], line['alias'], line['birth'][0], line['death'][0]
    print(osoba_1, alias_1, datetime.datetime.strptime(str(dob_1), '%Y%m%d').date(), "-", datetime.datetime.strptime(str(dod_1), '%Y%m%d').date())

print('---')
for line in vysledok2:
    osoba_2,  alias_2, dob_2, dod_2 = line['name'], line['alias'], line['birth'][0], line['death'][0]
    print(osoba_2, alias_2, datetime.datetime.strptime(str(dob_2), '%Y%m%d').date(), "-", datetime.datetime.strptime(str(dod_2), '%Y%m%d').date())
    

['Hiromi Wada'] ['Wada, Hiromi', '和田裕美', '裕美'] 1988-07-11 - 2088-07-11
---
['Ootaki, Yuuko'] ['Yuko Ohtaki', 'Yuko Ootaki'] 1963-03-19 - 2063-03-19


In [ ]:
def getDifference():
    